In [1]:
import pandas as pd
import numpy as np
import os
import sumolib
import copy
from tqdm import tqdm
from datetime import datetime

In [2]:
midnight = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
next_day = int(datetime(2024, 1, 6, 0, 0, 0).timestamp())
fmins = range(midnight, next_day, 300)
m = 105 # m ranges from 26 to 287
# sigtable 시작시각  : 현재시각 - 1200 = 08:25
# 시뮬레이션 시작시각 : 현재시각 - 900 = 08:30
# 시뮬레이션 종료시각 : 현재시각 - 600 = 08:35
# 현재시각           : 08:45
present_time = fmins[m]
sigtable_start = fmins[m] - 1200
sim_start = fmins[m] - 900
sim_end = fmins[m] - 600
print(datetime.fromtimestamp(sigtable_start))
print(datetime.fromtimestamp(sim_start))
print(datetime.fromtimestamp(sim_end))
print(datetime.fromtimestamp(present_time))
net = sumolib.net.readNet('../../Data/networks/sn.net.xml')
inter_node = pd.read_csv('../../data/tables/inter_node.csv', index_col=0)

2024-01-05 08:25:00
2024-01-05 08:30:00
2024-01-05 08:35:00
2024-01-05 08:45:00


In [3]:
histid = pd.read_csv(f'../../Data/tables/histids/histids_{fmins[50]}.csv', index_col=0)
print(sorted(histid.node_id.unique()))

['i0', 'i1', 'i2', 'i3', 'i6', 'i7', 'i8', 'i9']


In [4]:
inter2node = dict(zip(inter_node['inter_no'], inter_node['node_id']))
node2inter = dict(zip(inter_node['node_id'], inter_node['inter_no']))
ch2pa = {'u00': 'i0', 'u20': 'i2', 'u30': 'i3', 'u31': 'i3', 'u32': 'i3', 'c30': 'i3'}
pa2ch = {'i0':['u00'], 'i1':[], 'i2':['u20'], 'i3':['c30', 'u30', 'u31', 'u32'], 'i6':[], 'i7':[], 'i8':[], 'i9':[]}
node_ids = sorted(inter_node.node_id.unique())
parent_ids = sorted(inter_node[inter_node.inter_type=='parent'].node_id.unique())
child_ids = sorted(inter_node[inter_node.inter_type=='child'].node_id.unique())

print(inter2node)
print(node2inter)
print(ch2pa)
print(pa2ch)
print(node_ids)
print(parent_ids)
print(child_ids)

{175: 'u00', 176: 'i1', 177: 'u20', 178: 'c30', 210: 'u60', 206: 'i7', 201: 'i8', 202: 'i9'}
{'i0': 175, 'u00': 175, 'i1': 176, 'i2': 177, 'u20': 177, 'i3': 178, 'u30': 178, 'u31': 178, 'u32': 178, 'c30': 178, 'i6': 210, 'u60': 210, 'i7': 206, 'i8': 201, 'i9': 202}
{'u00': 'i0', 'u20': 'i2', 'u30': 'i3', 'u31': 'i3', 'u32': 'i3', 'c30': 'i3'}
{'i0': ['u00'], 'i1': [], 'i2': ['u20'], 'i3': ['c30', 'u30', 'u31', 'u32'], 'i6': [], 'i7': [], 'i8': [], 'i9': []}
['c30', 'i0', 'i1', 'i2', 'i3', 'i6', 'i7', 'i8', 'i9', 'u00', 'u20', 'u30', 'u31', 'u32', 'u60']
['i0', 'i1', 'i2', 'i3', 'i6', 'i7', 'i8', 'i9']
['c30', 'u00', 'u20', 'u30', 'u31', 'u32', 'u60']


In [5]:
print(fmins[m], datetime.fromtimestamp(fmins[m]))
histid = pd.read_csv(f'../../Data/tables/histids/histids_{fmins[m]}.csv', index_col=0)
match6 = pd.read_csv('../../Data/tables/matching/match6.csv', index_col=0)
histid = histid.reset_index(drop=True)
histid = histid.drop(columns=['inter_no'])
match6 = match6[['node_id', 'phase_no', 'ring_type', 'inc_edge', 'out_edge']].reset_index(drop=True)
display(histid)
display(match6)

1704411900 2024-01-05 08:45:00


node_id  start_unix  phas_A  phas_B  duration     inc_edge_A  \
0        i2  1704410739       1       1        40  -571542809_01   
1        i2  1704410739       2       2        25   571542811_02   
2        i2  1704410739       3       3        71            NaN   
3        i2  1704410739       4       4        34  -571542809_01   
4        i6  1704410760       1       1        24  -571542115_01   
..      ...         ...     ...     ...       ...            ...   
163      i0  1704411630       3       4        26   571545870_02   
164      i0  1704411630       4       4        33   571510153_02   
165      i1  1704411670       1       1        37  -571542810_01   
166      i1  1704411670       2       2        93  -571542810_01   
167      i1  1704411670       3       3        40   571543469_02   

           out_edge_A       inc_edge_B    out_edge_B  
0        571542811_01     571542811_02  571542809_01  
1        571542107_01    -571542809_01  571542809_01  
2                 NaN              NaN           NaN  
3        571542811_01     571542107_02  571542809_01  
4        571500535_01              NaN           NaN  
..                ...              ...           ...  
163      571510153_01     571510153_02  571545870_01  
164      571500487_01     571510153_02  571545870_01  
165  -571542797_02.99  571542797_02.99  571542810_01  
166  -571542797_02.99    -571542810_01  571543469_01  
167  -571542797_02.99              NaN           NaN  

[168 rows x 9 columns]

node_id  phase_no ring_type       inc_edge      out_edge
0        i0         1         A  -571542797_02  571500487_01
1        i0         1         B  -571500487_01  571542797_02
2        i0         2         A  -571500487_01  571545870_01
3        i0         2         B  -571542797_02  571510153_01
4        i0         3         A   571545870_02  571510153_01
..      ...       ...       ...            ...           ...
111     u60         2         B            NaN           NaN
112     u60         3         A            NaN           NaN
113     u60         3         B            NaN           NaN
114     u60         4         A            NaN           NaN
115     u60         4         B            NaN           NaN

[116 rows x 5 columns]

In [6]:
sorted(histid.node_id.unique())

['i0', 'i1', 'i2', 'i3', 'i6', 'i8', 'i9']

In [7]:
new_histids = []
for parent_id in parent_ids:
    for child_id in pa2ch[parent_id]:
        new_histid = histid.copy()[histid.node_id==parent_id]
        new_histid[['inc_edge_A', 'out_edge_A', 'inc_edge_B', 'out_edge_B']] = np.nan
        for i, row in new_histid.iterrows():
            phas_A = row.phas_A
            phas_B = row.phas_B
            new_match = match6[match6.node_id==child_id]
            Arow = new_match[(new_match.phase_no==phas_A) & (new_match.ring_type=='A')]
            if ~ Arow[['inc_edge', 'out_edge']].isna().all().all():
                inc_edge = Arow.iloc[0].inc_edge
                out_edge = Arow.iloc[0].out_edge
                new_histid.loc[i, ['inc_edge_A', 'out_edge_A']] = [inc_edge, out_edge]
            Brow = new_match[(new_match.phase_no==phas_B) & (new_match.ring_type=='B')]
            if ~ Brow[['inc_edge', 'out_edge']].isna().all().all():
                inc_edge = Brow.iloc[0].inc_edge
                out_edge = Brow.iloc[0].out_edge
                new_histid.loc[i, ['inc_edge_B', 'out_edge_B']] = [inc_edge, out_edge]
            new_histid.loc[i, 'node_id'] = child_id
        new_histids.append(new_histid)
histid_child = pd.concat(new_histids)
histids = pd.concat([histid.copy(), histid_child])
histids = histids.sort_values(by=['start_unix', 'node_id', 'phas_A', 'phas_B']).reset_index(drop=True)
display(histids)

node_id  start_unix  phas_A  phas_B  duration     inc_edge_A  \
0        i2  1704410739       1       1        40  -571542809_01   
1        i2  1704410739       2       2        25   571542811_02   
2        i2  1704410739       3       3        71            NaN   
3        i2  1704410739       4       4        34  -571542809_01   
4       u20  1704410739       1       1        40            NaN   
..      ...         ...     ...     ...       ...            ...   
313     u00  1704411630       3       4        26            NaN   
314     u00  1704411630       4       4        33            NaN   
315      i1  1704411670       1       1        37  -571542810_01   
316      i1  1704411670       2       2        93  -571542810_01   
317      i1  1704411670       3       3        40   571543469_02   

           out_edge_A       inc_edge_B    out_edge_B  
0        571542811_01     571542811_02  571542809_01  
1        571542107_01    -571542809_01  571542809_01  
2                 NaN              NaN           NaN  
3        571542811_01     571542107_02  571542809_01  
4                 NaN              NaN           NaN  
..                ...              ...           ...  
313               NaN              NaN           NaN  
314               NaN              NaN           NaN  
315  -571542797_02.99  571542797_02.99  571542810_01  
316  -571542797_02.99    -571542810_01  571543469_01  
317  -571542797_02.99              NaN           NaN  

[318 rows x 9 columns]

In [143]:
histids[histids.node_id=='u00']

node_id  start_unix  phas_A  phas_B  duration    inc_edge_A  \
18      u00  1704410780       1       1        40           NaN   
19      u00  1704410780       2       2        42  571500487_02   
20      u00  1704410780       3       3        29           NaN   
21      u00  1704410780       3       4        26           NaN   
22      u00  1704410780       4       4        33           NaN   
79      u00  1704410950       1       1        40           NaN   
80      u00  1704410950       2       2        42  571500487_02   
81      u00  1704410950       3       3        29           NaN   
82      u00  1704410950       3       4        26           NaN   
83      u00  1704410950       4       4        33           NaN   
146     u00  1704411120       1       1        40           NaN   
147     u00  1704411120       2       2        42  571500487_02   
148     u00  1704411120       3       3        29           NaN   
149     u00  1704411120       3       4        26           NaN   
150     u00  1704411120       4       4        33           NaN   
199     u00  1704411290       1       1        40           NaN   
200     u00  1704411290       2       2        42  571500487_02   
201     u00  1704411290       3       3        29           NaN   
202     u00  1704411290       3       4        26           NaN   
203     u00  1704411290       4       4        33           NaN   
257     u00  1704411460       1       1        40           NaN   
258     u00  1704411460       2       2        42  571500487_02   
259     u00  1704411460       3       3        29           NaN   
260     u00  1704411460       3       4        26           NaN   
261     u00  1704411460       4       4        33           NaN   
310     u00  1704411630       1       1        40           NaN   
311     u00  1704411630       2       2        42  571500487_02   
312     u00  1704411630       3       3        29           NaN   
313     u00  1704411630       3       4        26           NaN   
314     u00  1704411630       4       4        33           NaN   

          out_edge_A inc_edge_B out_edge_B  
18               NaN        NaN        NaN  
19   571500487_01.32        NaN        NaN  
20               NaN        NaN        NaN  
21               NaN        NaN        NaN  
22               NaN        NaN        NaN  
79               NaN        NaN        NaN  
80   571500487_01.32        NaN        NaN  
81               NaN        NaN        NaN  
82               NaN        NaN        NaN  
83               NaN        NaN        NaN  
146              NaN        NaN        NaN  
147  571500487_01.32        NaN        NaN  
148              NaN        NaN        NaN  
149              NaN        NaN        NaN  
150              NaN        NaN        NaN  
199              NaN        NaN        NaN  
200  571500487_01.32        NaN        NaN  
201              NaN        NaN        NaN  
202              NaN        NaN        NaN  
203              NaN        NaN        NaN  
257              NaN        NaN        NaN  
258  571500487_01.32        NaN        NaN  
259              NaN        NaN        NaN  
260              NaN        NaN        NaN  
261              NaN        NaN        NaN  
310              NaN        NaN        NaN  
311  571500487_01.32        NaN        NaN  
312              NaN        NaN        NaN  
313              NaN        NaN        NaN  
314              NaN        NaN        NaN

In [8]:
node_ids = sorted(histids.node_id.unique())
nodes = [net.getNode(node_id) for node_id in node_ids]
print(node_ids)
print(nodes)

['c30', 'i0', 'i1', 'i2', 'i3', 'i6', 'i8', 'i9', 'u00', 'u20', 'u30', 'u31', 'u32']
[<junction id="c30"/>, <junction id="i0"/>, <junction id="i1"/>, <junction id="i2"/>, <junction id="i3"/>, <junction id="i6"/>, <junction id="i8"/>, <junction id="i9"/>, <junction id="u00"/>, <junction id="u20"/>, <junction id="u30"/>, <junction id="u31"/>, <junction id="u32"/>]


In [9]:
node2init = {}
for node in nodes:
    node_id = node.getID()
    conns = [(c.getJunctionIndex(), c) for c in node.getConnections()]
    conns = [c for c in conns if c[0] >= 0]
    conns = sorted(conns, key=lambda x: x[0])
    state = []
    for i, ci in conns:
        if ci.getTLLinkIndex() < 0:
            continue
        are_foes = False
        for j, cj in conns:
            if ci.getTo() == cj.getTo():
                continue
            if node.areFoes(i, j):
                are_foes = True
                break
        state.append('r' if are_foes else 'g')
    node2init[node_id] = state

# 어떤 연결과도 상충이 일어나지는 않지만, 신호가 부여되어 있는 경우에는 r을 부여
for _, row in histids.iterrows():
    node_id = row['node_id']
    inc_edge_A = row.inc_edge_A
    inc_edge_B = row.inc_edge_B
    out_edge_A = row.out_edge_A
    out_edge_B = row.out_edge_B

    if pd.isna(inc_edge_A) or pd.isna(out_edge_A):
        pass
    else:
        inc_edge_A = net.getEdge(inc_edge_A)
        out_edge_A = net.getEdge(out_edge_A)
        for conn in inc_edge_A.getConnections(out_edge_A):
            index = conn.getTLLinkIndex()
            if index >= 0:
                node2init[node_id][index] = 'r'

    if pd.isna(inc_edge_B) or pd.isna(out_edge_B):
        pass
    else:
        inc_edge_B = net.getEdge(inc_edge_B)
        out_edge_B = net.getEdge(out_edge_B)
        for conn in inc_edge_B.getConnections(out_edge_B):
            index = conn.getTLLinkIndex()
            if index >= 0:
                node2init[node_id][index] = 'r'
for node_id in node_ids:
    print(node_id, "".join(node2init[node_id]))

c30 rrrrrr
i0 grrrgrrrgrrrrrgrr
i1 grrrrrrgrr
i2 rrggrrr
i3 grrrrgrrrrgrrrrgrrrr
i6 grrrgrrrrgrrgrrr
i8 grrrrrrrgrrrgrrr
i9 rrrr
u00 ggggrgggg
u20 ggrggg
u30 ggggrggg
u31 ggggrggg
u32 gggggggr


In [10]:
print(present_time)
print(datetime.fromtimestamp(present_time))
sigtable = histids.copy()
sigtable['init_state'] = sigtable['node_id'].map(node2init)
sigtable['state'] = sigtable['init_state'].map(lambda x:''.join(x))
for i, row in sigtable.iterrows():
    node_id = row.node_id
    inc_edge_A = row.inc_edge_A
    inc_edge_B = row.inc_edge_B
    out_edge_A = row.out_edge_A
    out_edge_B = row.out_edge_B
    state = copy.deepcopy(node2init)[node_id]

    if pd.isna(inc_edge_A) or pd.isna(out_edge_A):
        continue
    else:
        inc_edge_A = net.getEdge(inc_edge_A)
        out_edge_A = net.getEdge(out_edge_A)
        for conn in inc_edge_A.getConnections(out_edge_A):
            index = conn.getTLLinkIndex()
            if index >= 0:
                state[index] = 'G'
        sigtable.at[i, 'state'] = ''.join(state)

    if pd.isna(inc_edge_B) or pd.isna(out_edge_B):
        continue
    else:
        inc_edge_B = net.getEdge(inc_edge_B)
        out_edge_B = net.getEdge(out_edge_B)
        for conn in inc_edge_B.getConnections(out_edge_B):
            index = conn.getTLLinkIndex()
            if index >= 0:
                state[index] = 'G'
        sigtable.at[i, 'state'] = ''.join(state)
sigtable = sigtable.dropna(subset='state')
sigtable = sigtable.reset_index(drop=True)
sigtable['phase_sumo'] = sigtable.groupby(['node_id', 'start_unix']).cumcount()
sigtable = sigtable[sigtable.start_unix >= sigtable_start]
sigtable = sigtable[['node_id', 'start_unix', 'phase_sumo', 'duration', 'state']]
sigtable = sigtable.sort_values(by=['start_unix', 'node_id'])
sigtable['start_dt'] = sigtable['start_unix'].apply(lambda x:datetime.fromtimestamp(x))
display(sigtable)

1704411900
2024-01-05 08:45:00


node_id  start_unix  phase_sumo  duration       state            start_dt
0        i2  1704410739           0        40     GGggGGG 2024-01-05 08:25:39
1        i2  1704410739           1        25     rrggrrr 2024-01-05 08:25:39
2        i2  1704410739           2        71     rrggrrr 2024-01-05 08:25:39
3        i2  1704410739           3        34     rrggGGG 2024-01-05 08:25:39
4       u20  1704410739           0        40      ggrggg 2024-01-05 08:25:39
..      ...         ...         ...       ...         ...                 ...
313     u00  1704411630           3        26   ggggrgggg 2024-01-05 08:40:30
314     u00  1704411630           4        33   ggggrgggg 2024-01-05 08:40:30
315      i1  1704411670           0        37  gGGGGGrgrr 2024-01-05 08:41:10
316      i1  1704411670           1        93  grrGGGGgrr 2024-01-05 08:41:10
317      i1  1704411670           2        40  grrrrrrgGG 2024-01-05 08:41:10

[318 rows x 6 columns]

In [134]:
Sigtable = []
for node_id, group in sigtable.groupby('node_id'):
    new_rows_list = []
    for i in range(1, len(group)):
        prev_row = group.iloc[i-1:i].copy()
        next_row = group.iloc[i:i+1].copy()
        new_rows = pd.concat([prev_row, prev_row, next_row]).reset_index(drop=True)
        new_rows.loc[0, 'phase_sumo'] = str(prev_row.phase_sumo.iloc[0]) + '_g'
        new_rows.loc[0, 'duration'] = new_rows.loc[0, 'duration'] - 5
        new_rows.loc[1, 'phase_sumo'] = str(prev_row.phase_sumo.iloc[0]) + '_y'
        new_rows.loc[1, 'duration'] = 4
        yellow_state = ''
        red_state = ''
        for a, b in zip(prev_row.state.iloc[0], next_row.state.iloc[0]):
            if a == 'G' and b == 'r':
                yellow_state += 'y'
                red_state += 'r'
            else:
                yellow_state += a
                red_state += a
        new_rows.loc[2, 'phase_sumo'] = str(next_row.phase_sumo.iloc[0]) + '__r'
        new_rows.loc[2, 'duration'] = 1
        new_rows.loc[1, 'state'] = yellow_state
        new_rows.loc[2, 'state'] = red_state
        new_rows_list.append(new_rows)
    next_row['phase_sumo'] = str(next_row.phase_sumo.iloc[0]) + '_g'
    next_row['duration'] -= 5
    # next_row.loc['duration'] -= 5
    new_rows_list.append(next_row)
    new_rows = pd.concat(new_rows_list)
    Sigtable.append(new_rows)
Sigtable = pd.concat(Sigtable).sort_values(by=['node_id', 'start_unix', 'phase_sumo']).reset_index(drop=True)
Sigtable[:60]

node_id  start_unix phase_sumo  duration   state            start_dt
0      c30  1704410790        0_g        33  rrrrrr 2024-01-05 08:26:30
1      c30  1704410790        0_y         4  rrrrrr 2024-01-05 08:26:30
2      c30  1704410790       1__r         1  rrrrrr 2024-01-05 08:26:30
3      c30  1704410790        1_g        34  GGGGGG 2024-01-05 08:26:30
4      c30  1704410790        1_y         4  GGGGGG 2024-01-05 08:26:30
5      c30  1704410790       2__r         1  GGGGGG 2024-01-05 08:26:30
6      c30  1704410790        2_g        37  GGGGGG 2024-01-05 08:26:30
7      c30  1704410790        2_y         4  GGGGGG 2024-01-05 08:26:30
8      c30  1704410790       3__r         1  GGGGGG 2024-01-05 08:26:30
9      c30  1704410790        3_g        16  GGGGGG 2024-01-05 08:26:30
10     c30  1704410790        3_y         4  yyyyyy 2024-01-05 08:26:30
11     c30  1704410950       0__r         1  rrrrrr 2024-01-05 08:29:10
12     c30  1704410950        0_g        33  rrrrrr 2024-01-05 08:29:10
13     c30  1704410950        0_y         4  rrrrrr 2024-01-05 08:29:10
14     c30  1704410950       1__r         1  rrrrrr 2024-01-05 08:29:10
15     c30  1704410950        1_g        34  GGGGGG 2024-01-05 08:29:10
16     c30  1704410950        1_y         4  GGGGGG 2024-01-05 08:29:10
17     c30  1704410950       2__r         1  GGGGGG 2024-01-05 08:29:10
18     c30  1704410950        2_g        37  GGGGGG 2024-01-05 08:29:10
19     c30  1704410950        2_y         4  GGGGGG 2024-01-05 08:29:10
20     c30  1704410950       3__r         1  GGGGGG 2024-01-05 08:29:10
21     c30  1704410950        3_g        16  GGGGGG 2024-01-05 08:29:10
22     c30  1704410950        3_y         4  yyyyyy 2024-01-05 08:29:10
23     c30  1704411110       0__r         1  rrrrrr 2024-01-05 08:31:50
24     c30  1704411110        0_g        33  rrrrrr 2024-01-05 08:31:50
25     c30  1704411110        0_y         4  rrrrrr 2024-01-05 08:31:50
26     c30  1704411110       1__r         1  rrrrrr 2024-01-05 08:31:50
27     c30  1704411110        1_g        34  GGGGGG 2024-01-05 08:31:50
28     c30  1704411110        1_y         4  GGGGGG 2024-01-05 08:31:50
29     c30  1704411110       2__r         1  GGGGGG 2024-01-05 08:31:50
30     c30  1704411110        2_g        37  GGGGGG 2024-01-05 08:31:50
31     c30  1704411110        2_y         4  GGGGGG 2024-01-05 08:31:50
32     c30  1704411110       3__r         1  GGGGGG 2024-01-05 08:31:50
33     c30  1704411110        3_g        16  GGGGGG 2024-01-05 08:31:50
34     c30  1704411110        3_y         4  yyyyyy 2024-01-05 08:31:50
35     c30  1704411270       0__r         1  rrrrrr 2024-01-05 08:34:30
36     c30  1704411270        0_g        33  rrrrrr 2024-01-05 08:34:30
37     c30  1704411270        0_y         4  rrrrrr 2024-01-05 08:34:30
38     c30  1704411270       1__r         1  rrrrrr 2024-01-05 08:34:30
39     c30  1704411270        1_g        34  GGGGGG 2024-01-05 08:34:30
40     c30  1704411270        1_y         4  GGGGGG 2024-01-05 08:34:30
41     c30  1704411270       2__r         1  GGGGGG 2024-01-05 08:34:30
42     c30  1704411270        2_g        37  GGGGGG 2024-01-05 08:34:30
43     c30  1704411270        2_y         4  GGGGGG 2024-01-05 08:34:30
44     c30  1704411270       3__r         1  GGGGGG 2024-01-05 08:34:30
45     c30  1704411270        3_g        16  GGGGGG 2024-01-05 08:34:30
46     c30  1704411270        3_y         4  yyyyyy 2024-01-05 08:34:30
47     c30  1704411430       0__r         1  rrrrrr 2024-01-05 08:37:10
48     c30  1704411430        0_g        33  rrrrrr 2024-01-05 08:37:10
49     c30  1704411430        0_y         4  rrrrrr 2024-01-05 08:37:10
50     c30  1704411430       1__r         1  rrrrrr 2024-01-05 08:37:10
51     c30  1704411430        1_g        34  GGGGGG 2024-01-05 08:37:10
52     c30  1704411430        1_y         4  GGGGGG 2024-01-05 08:37:10
53     c30  1704411430       2__r         1  GGGGGG 2024-01-05 08:37:10
54     c30  1704411430        2_g        37

In [135]:
# sigtable 시작시각  : 현재시각 - 1200 = 08:25
# 시뮬레이션 시작시각 : 현재시각 - 900 = 08:30
# 시뮬레이션 종료시각 : 현재시각 - 600 = 08:35
# 현재시각           : 08:45
print(datetime.fromtimestamp(sigtable_start))
print(datetime.fromtimestamp(sim_start))
print(datetime.fromtimestamp(sim_end))
print(datetime.fromtimestamp(present_time))

2024-01-05 08:25:00
2024-01-05 08:30:00
2024-01-05 08:35:00
2024-01-05 08:45:00


In [137]:
for k, g in Sigtable.groupby('node_id'):
    print(k)

c30
i0
i1
i2
i3
i6
i8
i9
u00
u20
u30
u31
u32


In [140]:
offsets = {}
SIGTABLE = []
for node_id, group in Sigtable.groupby('node_id'):
    lsbs = group[group['start_unix'] < sim_start]['start_unix'].max() # the last start_unix before sim_start
    offsets[node_id] = lsbs - sim_start
    group = group[(group['start_unix'] < sim_end) & (group['start_unix'] >= lsbs)]
    SIGTABLE.append(group)
SIGTABLE = pd.concat(SIGTABLE)

strings = ['<additional>\n']
for node_id, group in Sigtable.groupby('node_id'):
    strings.append(f'    <tlLogic id="{node_id}" type="static" programID="{node_id}_prog" offset="{offsets[node_id]}">\n')
    for i, row in group.iterrows():
        duration = row.duration
        state = row.state
        strings.append(f'      <phase duration="{duration}" state="{state}"/>\n')
    strings.append('    </tlLogic>\n')
strings.append('</additional>')
strings = ''.join(strings)
# 저장
path_output = '../../Data/networks/sn.add.xml'
with open(path_output, 'w') as f:
    f.write(strings)

print(strings)

<additional>
    <tlLogic id="c30" type="static" programID="c30_prog" offset="-50">
      <phase duration="33" state="rrrrrr"/>
      <phase duration="4" state="rrrrrr"/>
      <phase duration="1" state="rrrrrr"/>
      <phase duration="34" state="GGGGGG"/>
      <phase duration="4" state="GGGGGG"/>
      <phase duration="1" state="GGGGGG"/>
      <phase duration="37" state="GGGGGG"/>
      <phase duration="4" state="GGGGGG"/>
      <phase duration="1" state="GGGGGG"/>
      <phase duration="16" state="GGGGGG"/>
      <phase duration="4" state="yyyyyy"/>
      <phase duration="1" state="rrrrrr"/>
      <phase duration="33" state="rrrrrr"/>
      <phase duration="4" state="rrrrrr"/>
      <phase duration="1" state="rrrrrr"/>
      <phase duration="34" state="GGGGGG"/>
      <phase duration="4" state="GGGGGG"/>
      <phase duration="1" state="GGGGGG"/>
      <phase duration="37" state="GGGGGG"/>
      <phase duration="4" state="GGGGGG"/>
      <phase duration="1" state="GGGGGG"/>
      